# DecisionTree Classification model: Predicting stock price movement

### Initial Imports

In [1]:
import numpy as np
import pandas as pd
import yfinance as yf
from dotenv import load_dotenv
import os
from finta import TA
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, accuracy_score, classification_report
from sklearn.tree import DecisionTreeClassifier
from sklearn.preprocessing import StandardScaler
from sklearn import tree
from sklearn.decomposition import PCA
import graphviz
import pydotplus
from IPython.display import Image
load_dotenv()


True

### Obtaining Historical Stock Data

In [2]:
data = yf.download("OLLI", start="2000-01-01",
                    end="2022-03-10", group_by='tickers')

data.columns= data.columns.str.lower()

data.head()

[*********************100%***********************]  1 of 1 completed


open       high        low      close  adj close    volume
Date                                                                   
2015-07-16  22.68  22.990000  20.570000  21.150000  21.150000  12591100
2015-07-17  21.24  21.350000  20.000000  20.040001  20.040001   1260500
2015-07-20  20.40  21.180000  19.580000  20.200001  20.200001    485600
2015-07-21  20.00  20.450001  19.620001  20.000000  20.000000    207700
2015-07-22  20.00  20.820000  20.000000  20.650000  20.650000    199700

In [3]:
ohlc = data.copy()

### Let's create our technical indicators
We will use the technical indicators as input features in our classification model

In [4]:
short_window=10
long_window_sma=30
long_window_ema = 50

#Simple Moving Average - 10 days
ohlc["SMA10"] = TA.SMA(ohlc, short_window)
#Simple Moving Average - 30 days
ohlc["SMA30"] = TA.SMA(ohlc, long_window_sma)
#Exponential Moving Average - 10 days
ohlc["EMA10"] = TA.EMA(ohlc, short_window)
#Exponential Moving Average - 30 days
ohlc["EMA50"] = TA.EMA(ohlc, long_window_ema)
#Awesome Oscillator
ohlc["AO"] = TA.AO(ohlc)
#Average True Range
ohlc['ATR'] = TA.ATR(ohlc)
#Average Directional Index
ohlc['ADX'] = TA.ADX(ohlc)
#Relative Strenght Index
ohlc['RSI'] = TA.RSI(ohlc)
#Moving Average Convergence Divergence
macd = TA.MACD(ohlc, period_fast=12, period_slow=26, signal=9, column="close")
ohlc['MACD'] = macd['MACD']
ohlc['MACDsignal'] = macd['SIGNAL']


### Let's create our target 'y' values
The "return" column values will be used to create our binary target values.  We are shifting the values "up" one period so that our features are aligned with the next period return, as this is the value we are trying to predict.

In [5]:
ohlc['returns'] = ohlc['close'].pct_change(1).shift(-1)

#this is our target column: The values will depend on whether returns we calculated above were positive or negative.
ohlc['target_cls'] = np.where(ohlc.returns > 0, 1, 0)

In [6]:
#drop all NaN values from dataframe
ohlc.dropna(inplace=True)

display(ohlc.isnull().value_counts())

display(ohlc.head(10))

#Let's check if our dataset is balanced
print("Number of observations")
display(ohlc.target_cls.value_counts())

open   high   low    close  adj close  volume  SMA10  SMA30  EMA10  EMA50  AO     ATR    ADX    RSI    MACD   MACDsignal  returns  target_cls
False  False  False  False  False      False   False  False  False  False  False  False  False  False  False  False       False    False         1641
dtype: int64

open       high        low      close  adj close  volume  \
Date                                                                        
2015-09-01  17.620001  18.045000  17.260000  17.549999  17.549999  126500   
2015-09-02  17.920000  17.969999  16.980000  17.100000  17.100000  380000   
2015-09-03  17.070000  17.639999  16.219999  16.610001  16.610001  365500   
2015-09-04  16.309999  17.290001  16.309999  17.030001  17.030001  185200   
2015-09-08  17.469999  17.809999  16.950001  17.270000  17.270000  236900   
2015-09-09  17.290001  18.270000  16.997999  17.090000  17.090000  326100   
2015-09-10  17.480000  18.740000  17.309999  18.250000  18.250000  582100   
2015-09-11  18.500000  18.780001  17.709999  18.260000  18.260000  498300   
2015-09-14  18.240000  18.450001  17.780001  18.100000  18.100000  405800   
2015-09-15  18.190001  18.440001  17.740000  18.190001  18.190001  238400   

             SMA10      SMA30      EMA10      EMA50        AO       ATR  \
Date                                                                      
2015-09-01  17.645  19.135000  17.734269  18.862924 -2.236162  1.058928   
2015-09-02  17.374  19.016667  17.618844  18.771167 -1.907544  1.071071   
2015-09-03  17.081  18.891333  17.435284  18.660107 -1.783897  1.098928   
2015-09-04  16.952  18.792333  17.361553  18.577346 -1.740603  1.080714   
2015-09-08  17.007  18.702333  17.344899  18.511729 -1.680515  1.082857   
2015-09-09  17.125  18.615000  17.298535  18.441146 -1.602568  1.116571   
2015-09-10  17.298  18.566667  17.471585  18.431754 -1.416391  1.199428   
2015-09-11  17.462  18.522000  17.614972  18.423398 -1.091774  1.171571   
2015-09-14  17.515  18.471333  17.703178  18.407812 -0.796126  1.105143   
2015-09-15  17.545  18.381667  17.791707  18.397407 -0.604494  1.009429   

                  ADX        RSI      MACD  MACDsignal   returns  target_cls  
Date                                                                          
2015-09-01  47.568801  40.419299 -0.626209   -0.527681 -0.025641           0  
2015-09-02  46.390902  37.676655 -0.634115   -0.548976 -0.028655           0  
2015-09-03  46.207650  34.899683 -0.669845   -0.573158  0.025286           1  
2015-09-04  46.043010  39.046688 -0.658371   -0.590205  0.014093           1  
2015-09-08  44.561789  41.345986 -0.623623   -0.596890 -0.010423           0  
2015-09-09  42.240136  40.123500 -0.602968   -0.598106  0.067876           1  
2015-09-10  39.311307  50.318255 -0.491267   -0.576735  0.000548           1  
2015-09-11  36.584472  50.396664 -0.397425   -0.540869 -0.008762           0  
2015-09-14  34.105797  49.062483 -0.331702   -0.499032  0.004972           1  
2015-09-15  31.928879  49.866471 -0.269506   -0.453124  0.026938           1

Number of observations


1    871
0    770
Name: target_cls, dtype: int64

### Encoded Signals
The values of some of our technical indicators need to be transformed into categorical data points in order to extract the signal from them.

In [7]:
ohlc['signalSMA10'] = np.where(ohlc['close'] > ohlc['SMA10'], 1, 0)

ohlc['signalSMA10/30'] = np.where(ohlc['SMA10'] > ohlc['SMA30'], 1, 0)

ohlc['signalEMA10'] = np.where(ohlc['close'] > ohlc['EMA10'], 1, 0)

ohlc ['signalEMA10/50'] = np.where(ohlc['EMA10'] > ohlc['EMA50'], 1, 0)

ohlc['MACDSIG'] = np.where(ohlc['MACDsignal'] > ohlc['MACD'], 1, 0)

ohlc.head()

open       high        low      close  adj close  volume  \
Date                                                                        
2015-09-01  17.620001  18.045000  17.260000  17.549999  17.549999  126500   
2015-09-02  17.920000  17.969999  16.980000  17.100000  17.100000  380000   
2015-09-03  17.070000  17.639999  16.219999  16.610001  16.610001  365500   
2015-09-04  16.309999  17.290001  16.309999  17.030001  17.030001  185200   
2015-09-08  17.469999  17.809999  16.950001  17.270000  17.270000  236900   

             SMA10      SMA30      EMA10      EMA50  ...        RSI      MACD  \
Date                                                 ...                        
2015-09-01  17.645  19.135000  17.734269  18.862924  ...  40.419299 -0.626209   
2015-09-02  17.374  19.016667  17.618844  18.771167  ...  37.676655 -0.634115   
2015-09-03  17.081  18.891333  17.435284  18.660107  ...  34.899683 -0.669845   
2015-09-04  16.952  18.792333  17.361553  18.577346  ...  39.046688 -0.658371   
2015-09-08  17.007  18.702333  17.344899  18.511729  ...  41.345986 -0.623623   

            MACDsignal   returns  target_cls  signalSMA10  signalSMA10/30  \
Date                                                                        
2015-09-01   -0.527681 -0.025641           0            0               0   
2015-09-02   -0.548976 -0.028655           0            0               0   
2015-09-03   -0.573158  0.025286           1            0               0   
2015-09-04   -0.590205  0.014093           1            1               0   
2015-09-08   -0.596890 -0.010423           0            1               0   

            signalEMA10  signalEMA10/50  MACDSIG  
Date                                              
2015-09-01            0               0        1  
2015-09-02            0               0        1  
2015-09-03            0               0        1  
2015-09-04            0               0        1  
2015-09-08            0               0        1  

[5 rows x 23 columns]

## Building our classification model

We need to create a new dataframe that contains all our features and target values.

In [8]:
features = ["AO","ATR", "ADX", "RSI", "MACDSIG", "signalSMA10", "signalSMA10/30", "signalEMA10",'signalEMA10/50']

features_df = ohlc[features]

targets = ohlc.target_cls

features_df.head()

AO       ATR        ADX        RSI  MACDSIG  signalSMA10  \
Date                                                                         
2015-09-01 -2.236162  1.058928  47.568801  40.419299        1            0   
2015-09-02 -1.907544  1.071071  46.390902  37.676655        1            0   
2015-09-03 -1.783897  1.098928  46.207650  34.899683        1            0   
2015-09-04 -1.740603  1.080714  46.043010  39.046688        1            1   
2015-09-08 -1.680515  1.082857  44.561789  41.345986        1            1   

            signalSMA10/30  signalEMA10  signalEMA10/50  
Date                                                     
2015-09-01               0            0               0  
2015-09-02               0            0               0  
2015-09-03               0            0               0  
2015-09-04               0            0               0  
2015-09-08               0            0               0

### Principal Component Analysys (PCA)
Let's also reduce the dimensionality of our data set and test if this improved the accuracy of our classification model

In [9]:
features_scaled = StandardScaler().fit_transform(features_df)

pca = PCA(n_components=6)

# Get 3 principal components for the ohlc data.
ohlc_pca = pca.fit_transform(features_scaled)

### Splitting data to train and test our model

We need to create two train&test subdata sets. One for the original dataset and the other for our PCA dataset.

In [10]:
X = features_df.copy()

y=targets.copy()

X_pca= features_scaled.copy()

y_pca = targets.copy()

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20, random_state=78)

X_train_pca, X_test_pca, y_train_pca, y_test_pca = train_test_split(X_pca, y_pca, test_size=0.20, random_state=78)

display(X_train.shape)
display(y_train.shape)
display(X_test.shape)
display(y_test.shape)

(1312, 9)

(1312,)

(329, 9)

(329,)

### Building a Decision Tree

Let's instantiate the model using sklearn and make predictions

In [11]:
model = DecisionTreeClassifier()

In [12]:
model = model.fit(X_train, y_train)
model_pca= model.fit(X_train_pca, y_train_pca)

In [13]:
predictions = model.predict(X_test)
predictions_pca = model_pca.predict(X_test_pca)

## Evaluating our model's effectiveness


### Accuracy score

We rely on the accuracy score as the primary performance metric since we want to know simply how accurate our model is in predicting the next daily return whether positive or negative.

In [14]:
acc_score = accuracy_score(y_test, predictions)
acc_score_pca= accuracy_score(y_test_pca, predictions_pca)

print("Accuracy Score")
print(acc_score)
print("Accuracy Score PCA")
print(acc_score_pca)

Accuracy Score
0.5227963525835866
Accuracy Score PCA
0.46808510638297873


### Classification report

### Visualising the Decision Tree

In [15]:
#Create DOT data
dot_data = tree.export_graphviz(
    model, out_file=None, feature_names=X.columns, class_names=["0", "1"], filled=True
)

# Draw graph
graph = pydotplus.graph_from_dot_data(dot_data)


# Show graph
Image(graph.create_png())

# Conclusion

- Unfortunately our daily return predictive model was not very succesful as it did not do better than a random guess.
 - It is well known that predicting stock returns is not exactly easy but perhaps the model would've worked better if:
 - we had access to a larger amount of historical data(OLLI only started trading in 2015) to train our model
 - and more importanly if we could improve the features selection. In our case, applying PCA was not very helpful in improving the model's performance.

- We would not rely on this model as part of our 3 components strategy.